In [ ]:
%tensorflow_version 1.x

TensorFlow 1.x selected.


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
import tensorflow as tf
from tqdm import tqdm
import os
import sys
import numpy as np
import glob
import pandas as pd
import cv2
import random
import matplotlib.pyplot as plt

In [ ]:
def homography_model(img, image_size, batch_size):
  x = tf.layers.conv2d(inputs=img, name='Conv2D1', padding='same',filters=64, kernel_size=[3,3], activation=None)
  x = tf.layers.batch_normalization(x, name='BatchNorm1')
  x = tf.nn.relu(x, name='Relu1')

  x = tf.layers.conv2d(inputs=x, name='Conv2D2', padding='same',filters=64, kernel_size=[3,3], activation=None) 
  x = tf.layers.batch_normalization(x, name='BatchNorm2')
  x = tf.nn.relu(x, name='Relu2')

  x = tf.layers.max_pooling2d(inputs=x, pool_size=[2,2], strides=2)

  x = tf.layers.conv2d(inputs=x, name='Conv2D3', padding='same',filters=64, kernel_size=[3,3], activation=None)
  x = tf.layers.batch_normalization(x, name='BatchNorm3')
  x = tf.nn.relu(x, name='Relu3')

  x = tf.layers.conv2d(inputs=x, name='Conv2D4', padding='same',filters=64, kernel_size=[3,3], activation=None)
  x = tf.layers.batch_normalization(x, name='BatchNorm4')
  x = tf.nn.relu(x, name='Relu4')

  x = tf.layers.max_pooling2d(inputs=x, pool_size=[2,2], strides=2)

  x = tf.layers.conv2d(inputs=x, name='Conv2D5', padding='same',filters=128, kernel_size=[3,3], activation=None)
  x = tf.layers.batch_normalization(x, name='BatchNorm5')
  x = tf.nn.relu(x, name='Relu5')

  x = tf.layers.conv2d(inputs=x, name='Conv2D6', padding='same',filters=128, kernel_size=[3,3], activation=None)
  x = tf.layers.batch_normalization(x, name='BatchNorm6')
  x = tf.nn.relu(x, name='Relu6')

  x = tf.layers.max_pooling2d(inputs=x, pool_size=[2,2], strides=2)

  x = tf.layers.conv2d(inputs=x, name='Conv2D7', padding='same',filters=128, kernel_size=[3,3], activation=None)
  x = tf.layers.batch_normalization(x, name='BatchNorm7')
  x = tf.nn.relu(x, name='Relu7')

  x = tf.layers.conv2d(inputs=x, name='Conv2D8', padding='same',filters=128, kernel_size=[3,3], activation=None)
  x = tf.layers.batch_normalization(x, name='BatchNorm8')
  x = tf.nn.relu(x, name='Relu8')

  #flattening layer
  x = tf.contrib.layers.flatten(x)

  #Fully-connected layers
  x = tf.layers.dense(inputs=x, name='FC1',units=1024, activation=tf.nn.relu)
  x = tf.layers.dropout(x,rate=0.5, training=True,name='Dropout')
  x = tf.layers.batch_normalization(x, name='BatchNorm9')
  H4 = tf.layers.dense(inputs=x, name='FCfinal',units=8, activation=None)

  return H4

In [ ]:
def PrettyPrint(NumEpochs, DivTrain, MiniBatchSize, NumTrainSamples, LatestFile):
	"""
	Prints all stats with all arguments
	"""
	print('Number of Epochs Training will run for ' + str(NumEpochs))
	print('Factor of reduction in training data is ' + str(DivTrain))
	print('Mini Batch Size ' + str(MiniBatchSize))
	print('Number of Training Images ' + str(NumTrainSamples))
	if LatestFile is not None:
		print('Loading latest checkpoint with the name ' + LatestFile)   

In [ ]:
def GenerateBatch(train_files_pa, train_files_pb, TrainLabels, MiniBatchSize):

  patches_ab = []
  labels = []

  for i in range(MiniBatchSize):
    index = random.randint(0, len(train_files_pa)-1) 
    patch_a = cv2.imread(train_files_pa[i], cv2.IMREAD_GRAYSCALE)
    patch_b = cv2.imread(train_files_pb[i], cv2.IMREAD_GRAYSCALE)

    patch_a = np.float32(patch_a)
    patch_b = np.float32(patch_b)  

    #combine images along depth
    patch_ab = np.dstack((patch_a, patch_b))     
    labels.append(TrainLabels[i,:].reshape(8,))
    patches_ab.append(patch_ab)

  return np.array(patches_ab), np.array(labels)

In [ ]:
def TrainOperation(ImgPH, LabelPH,CornerPH, I2PH, I1FullPH, train_files_PA, train_files_PB, train_labels, NumTrainSamples, ImageSize,
  NumEpochs, MiniBatchSize, SaveCheckPoint, CheckPointPath,
  DivTrain, LatestFile, LogsPath):
  """
  Inputs: 
  ImgPH is the Input Image placeholder
  LabelPH is the one-hot encoded label placeholder
  DirNamesTrain - Variable with Subfolder paths to train files
  TrainLabels - Labels corresponding to Train/Test
  NumTrainSamples - length(Train)
  ImageSize - Size of the image
  NumEpochs - Number of passes through the Train data
  MiniBatchSize is the size of the MiniBatch
  SaveCheckPoint - Save checkpoint every SaveCheckPoint iteration in every epoch, checkpoint saved automatically after every epoch
  CheckPointPath - Path to save checkpoints/model
  DivTrain - Divide the data by this number for Epoch calculation, use if you have a lot of dataor for debugging code
  LatestFile - Latest checkpointfile to continue training
  BasePath - Path to COCO folder without "/" at the end
  LogsPath - Path to save Tensorboard Logs
  ModelType - Supervised or Unsupervised Model
  Outputs:
  Saves Trained network in CheckPointPath and Logs to LogsPath
  """      
  # Predict output with forward pass
  print("Supervised")
  H4pt = homography_model(ImgPH, ImageSize, MiniBatchSize)

  with tf.name_scope('Loss'):
    loss = tf.sqrt(tf.reduce_sum((tf.squared_difference(H4pt,LabelPH))))

  with tf.name_scope('Adam'):
    Optimizer = tf.train.AdamOptimizer(learning_rate=1e-4).minimize(loss)

  # Tensorboard
  # Create a summary to monitor loss tensor
  EpochLossPH = tf.placeholder(tf.float32, shape=None)
  loss_summary = tf.summary.scalar('LossEveryIter', loss)
  epoch_loss_summary = tf.summary.scalar('LossPerEpoch', EpochLossPH)
  # tf.summary.image('Anything you want', AnyImg)

  # Merge all summaries into a single operation
  MergedSummaryOP1 = tf.summary.merge([loss_summary])
  MergedSummaryOP2 = tf.summary.merge([epoch_loss_summary])
  # MergedSummaryOP = tf.summary.merge_all()

  # Setup Saver
  Saver = tf.train.Saver()
  AccOverEpochs=np.array([0,0])
  with tf.Session() as sess:       
    if LatestFile is not None:
      Saver.restore(sess, CheckPointPath + LatestFile + '.ckpt')
    # Extract only numbers from the name
      StartEpoch = int(''.join(c for c in LatestFile.split('a')[0] if c.isdigit()))
      print('Loaded latest checkpoint with the name ' + LatestFile + '....')
    else:
      sess.run(tf.global_variables_initializer())
      StartEpoch = 0
      print('New model initialized....')

    # Tensorboard
    Writer = tf.summary.FileWriter(LogsPath, graph=tf.get_default_graph())

    for Epochs in tqdm(range(StartEpoch, NumEpochs)):
      NumIterationsPerEpoch = int(NumTrainSamples/MiniBatchSize/DivTrain)
      Loss=[]
      write_loss=[]
      epoch_loss=0
      for PerEpochCounter in tqdm(range(NumIterationsPerEpoch)):
        ImgBatch,LabelBatch = GenerateBatch(train_files_PA, train_files_PB, train_labels, MiniBatchSize)
        FeedDict = {ImgPH: ImgBatch, LabelPH: LabelBatch}

        _, LossThisBatch, Summary = sess.run([Optimizer, loss, MergedSummaryOP1], feed_dict=FeedDict)
        Loss.append(LossThisBatch)
        epoch_loss = epoch_loss + LossThisBatch
        # Save checkpoint every some SaveCheckPoint's iterations
        if PerEpochCounter % SaveCheckPoint == 0:
          # Save the Model learnt in this epoch
          SaveName =  CheckPointPath + str(Epochs) + 'a' + str(PerEpochCounter) + 'model.ckpt'
          Saver.save(sess,  save_path=SaveName)
          print('\n' + SaveName + ' Model Saved...')

        # Tensorboard
      epoch_loss = epoch_loss/NumIterationsPerEpoch
      print('The loss is ' ,np.mean(Loss))
      write_loss.append(np.mean(Loss))
      # Save model every epoch
      SaveName = CheckPointPath + str(Epochs) + 'model.ckpt'
      Saver.save(sess, save_path=SaveName)
      print('\n' + SaveName + ' Model Saved...')
      Summary_epoch = sess.run(MergedSummaryOP2,feed_dict={EpochLossPH: epoch_loss})
      Writer.add_summary(Summary_epoch,Epochs)
      Writer.flush()
    np.savetxt(LogsPath + "losshistory_supervised.txt", np.array(write_loss), delimiter = ",")

In [ ]:
def FindLatestModel(CheckPointPath):
    FileList = glob.glob(CheckPointPath + '*.ckpt.index') # * means all if need specific format then *.csv
    LatestFile = max(FileList, key=os.path.getctime)
    # Strip everything else except needed information
    LatestFile = LatestFile.replace(CheckPointPath, '')
    LatestFile = LatestFile.replace('.ckpt.index', '')
    return LatestFile

In [ ]:
def main():
  """
  Inputs: 
  None
  Outputs:
  Runs the Training and testing code based on the Flag
  """
  # Parse Command Line arguments
  # Parser = argparse.ArgumentParser()
  # Parser.add_argument('--BasePath', default='../Data', help='Base path of images, Default:/media/nitin/Research/Homing/SpectralCompression/COCO')
  # Parser.add_argument('--CheckPointPath', default='../Checkpoints/', help='Path to save Checkpoints, Default: ../Checkpoints/')
  # Parser.add_argument('--ModelType', default='unsup', help='Model type, Supervised or Unsupervised? Choose from Sup and Unsup, Default:Unsup')
  # Parser.add_argument('--NumEpochs', type=int, default=50, help='Number of Epochs to Train for, Default:50')
  # Parser.add_argument('--DivTrain', type=int, default=1, help='Factor to reduce Train data by per epoch, Default:1')
  # Parser.add_argument('--MiniBatchSize', type=int, default=64, help='Size of the MiniBatch to use, Default:1')
  # Parser.add_argument('--LoadCheckPoint', type=int, default=0, help='Load Model from latest Checkpoint from CheckPointsPath?, Default:0')
  # Parser.add_argument('--LogsPath', default='Logs/', help='Path to save Logs for Tensorboard, Default=Logs/')

  # Args = Parser.parse_args()
  # NumEpochs = Args.NumEpochs
  # BasePath = Args.BasePath
  # DivTrain = float(Args.DivTrain)
  # MiniBatchSize = Args.MiniBatchSize
  # LoadCheckPoint = Args.LoadCheckPoint
  # CheckPointPath = Args.CheckPointPath
  # LogsPath = Args.LogsPath
  # ModelType = Args.ModelType

  ModelType = 'sup'

  NumEpochs = 20
  DivTrain = 1
  MiniBatchSize = 1
  LoadCheckPoint = 0
  # Parser.add_argument('--LogsPath', default='../Logs/', help='Path to save Logs for Tensorboard, Default=Logs/')

  DivTrain = float(DivTrain)
  batch_size = 50
  CheckPointPath = '/content/drive/MyDrive/Project_1/supervised_checkpoints/'
  LogsPath = '/content/drive/MyDrive/Project_1/supervised_logs/'
  ImageSize = [128,128,1]
  SaveCheckPoint = 100

  # Setup all needed parameters including file reading
  patchSize = 128
  # Find Latest Checkpoint File
  if LoadCheckPoint==1:
    LatestFile = FindLatestModel(CheckPointPath)
  else:
    LatestFile = None

  ImgPH = tf.placeholder(tf.float32, shape=(MiniBatchSize, patchSize, patchSize, 2))
  NumTrainSamples = 20000

  # Pretty print stats
  PrettyPrint(NumEpochs, DivTrain, MiniBatchSize, NumTrainSamples, LatestFile)
  if(not (os.path.isdir(LogsPath))):
    print(LogsPath, "  was not present, creating the folder...")
    os.makedirs(LogsPath)

  print(" Supervised  Model Training using Tensorflow ...")

  if(not (os.path.isdir(CheckPointPath))):
    print(CheckPointPath, "  was not present, creating the folder...")
    os.makedirs(CheckPointPath)

  # files_in_dir, SaveCheckPoint, ImageSize, NumTrainSamples, _ = SetupAll(BasePath, CheckPointPath)
  train_files_PA = glob.glob( '/content/drive/MyDrive/Project_1/S_train/P_A'+ '/*.jpg')
  train_files_PB = glob.glob( '/content/drive/MyDrive/Project_1/S_train/P_B'+ '/*.jpg')
  image_files = glob.glob( '/content/drive/MyDrive/Project_1/S_train/I_A'+ '/*.jpg')
  NumTrainSamples = len(train_files_PA)
  train_labels = pd.read_csv('/content/drive/MyDrive/Project_1/S_train/H_4pt.csv', index_col = False)
  train_labels = train_labels.to_numpy()
  print("Number of Training Samples:..", NumTrainSamples)


  # Define PlaceHolder variables for Input and Predicted output

  LabelPH = tf.placeholder(tf.float32, shape=(MiniBatchSize, 8))
  CornerPH = tf.placeholder(tf.float32, shape=(MiniBatchSize, 4,2))
  I2PH = tf.placeholder(tf.float32, shape=(MiniBatchSize, 128, 128,1))
  I1FullPH = tf.placeholder(tf.float32, shape=(MiniBatchSize, ImageSize[0], ImageSize[1],ImageSize[2]))




  TrainOperation(ImgPH, LabelPH,CornerPH, I2PH, I1FullPH, train_files_PA, train_files_PB, train_labels, NumTrainSamples, ImageSize,
  NumEpochs, MiniBatchSize, SaveCheckPoint, CheckPointPath,
  DivTrain, LatestFile, LogsPath)

In [ ]:
tf.compat.v1.reset_default_graph()

In [ ]:
if __name__ == '__main__':
  main()

Number of Epochs Training will run for 20
Factor of reduction in training data is 1.0
Mini Batch Size 1
Number of Training Images 20000
 Supervised  Model Training using Tensorflow ...
Number of Training Samples:.. 5000
Supervised
New model initialized....


  0%|          | 4/5000 [00:05<1:34:06,  1.13s/it]


/content/drive/MyDrive/Project_1/supervised_checkpoints/0a0model.ckpt Model Saved...



  2%|▏         | 104/5000 [00:12<13:54,  5.87it/s]


/content/drive/MyDrive/Project_1/supervised_checkpoints/0a100model.ckpt Model Saved...


...


/content/drive/MyDrive/Project_1/supervised_checkpoints/19a4900model.ckpt Model Saved...



100%|██████████| 5000/5000 [07:31<00:00, 11.07it/s]


The loss is  0.0034300839


100%|██████████| 20/20 [2:25:10<00:00, 435.55s/it]


/content/drive/MyDrive/Project_1/supervised_checkpoints/19model.ckpt Model Saved...
